In [1]:
from scipy.linalg import expm
import qorelib as q
import numpy as np
from numpy import matrix, complexfloating, array
from numpy._typing import NDArray
from tqdm import tqdm
from scipy.optimize import leastsq
import plotly.graph_objects as go

In [2]:
OmegaQ01: float = 2 * np.pi * 5000
OmegaD: float = 2 * np.pi * 5000 + 2 * np.pi * 1  # 这个频率是角频率
# a: complexfloating = 1
# b: complexfloating = 0
a: complexfloating = np.sqrt(2) / 2
b: complexfloating = np.sqrt(2) / 2
A: float = 30 * 2 * np.pi * 1
PhiD: float = np.pi / 2 * 0


initialState: matrix = matrix([[a], [b]])

In [3]:
def HamiltonianWithoutDrive2X2(omegaQ01: float, omegaD: float):
    delta: float = omegaD - omegaQ01
    H: matrix = matrix([[0, 0], [0, -delta]])
    return H


def HamiltonianWithDrive2X2(omegaQ01: float, omegaD: float, phiD: float, A: float):
    delta: float = omegaD - omegaQ01
    H: matrix = matrix(
        [[0, 0.5 * A * np.exp(1j * phiD)], [0.5 * A * np.exp(-1j * phiD), -delta]]
    )
    return H

# Rabi Oscillation

In [4]:
data: NDArray = np.array([[0.0, 0.0]])
stateData: NDArray = np.array([[1.0j, 1.0j]])
τ: float = 0.3
precision: int = 1000
for t in tqdm(range(0, int(τ * precision)), desc="Computing ... ", colour="#12c462"):
    td = t / precision
    currentState: matrix = q.ComputeState(
        initialState, td, HamiltonianWithDrive2X2(OmegaQ01, OmegaD, PhiD, A)
    )
    if t == 0:
        stateData[0] = np.array(currentState.T)
    else:
        stateData = np.r_[stateData, currentState.T]
    if t == 0:
        data[0] = np.array([td, q.ComputeStateProbability(currentState, 0)])
    else:
        data = np.r_[data, np.array([[td, q.ComputeStateProbability(currentState, 0)]])]

Computing ... : 100%|██████████| 300/300 [00:00<00:00, 9045.56it/s]


In [5]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=data[:, 0], y=data[:, 1], name="0态概率", mode="markers"))
fig.update_yaxes(
    range=[-0.1, 1.1],
    dtick=0.5,
)
fig.update_layout(
    title={"text": "Rabi振荡", "y": 0.9, "x": 0.5, "xanchor": "center", "yanchor": "top"},
    xaxis_title="t(μs)",
    yaxis_title="0态概率",
    font=dict(color="black"),
    width=800,
)
fig.show()

# Ramsey fringe

Draw trace


In [6]:
omegaQ01_M = OmegaQ01

T: float = (2 * np.pi) / A
t_1: float = T / 4
numerator: float = 1.0
denominator: float = 3.0
τ: float = ((OmegaD - OmegaQ01) * numerator) / ((2 * np.pi) * denominator)
t_2: float = T / 4

stateData_drive1: NDArray = array([[1.0j, 1.0j]])
computedData_drive1: NDArray = array([[0.0, 0.0]])
stateData_nodrive: NDArray = array([[1.0j, 1.0j]])
computedData_nodrive: NDArray = array([[0.0, 0.0]])
stateData_drive2: NDArray = array([[1.0j, 1.0j]])
computedData_drive2: NDArray = array([[0.0, 0.0]])

# switcher
i, j, k = True, True, True

chooser = 0

precision: int = 50000
t_full = t_1 + τ + t_2
for t in tqdm(range(0, int(t_full * precision)), desc="Computing ... ", colour="red"):
    t_precise: float = t / precision
    if t_precise <= t_1:
        if i:
            i = not i
            currentState: matrix = q.ComputeState(
                initialState,
                1 / precision,
                HamiltonianWithDrive2X2(omegaQ01_M, OmegaD, PhiD, A),
            )
            stateData_drive1[0] = np.array(currentState.T)
            computedData_drive1[0] = np.array(
                [t_precise, q.ComputeStateProbability(currentState, chooser)]
            )
        else:
            currentState: matrix = q.ComputeState(
                currentState,
                1 / precision,
                HamiltonianWithDrive2X2(omegaQ01_M, OmegaD, PhiD, A),
            )
            stateData_drive1 = np.r_[stateData_drive1, currentState.T]
            computedData_drive1 = np.r_[
                computedData_drive1,
                np.array(
                    [[t_precise, q.ComputeStateProbability(currentState, chooser)]]
                ),
            ]
    if t_precise > t_1 and t_precise <= (t_1 + τ):
        currentState: matrix = q.ComputeState(
            currentState, 1 / precision, HamiltonianWithoutDrive2X2(omegaQ01_M, OmegaD)
        )
        if j:
            j = not j
            stateData_nodrive[0] = np.array(currentState.T)
            computedData_nodrive[0] = np.array(
                [t_precise, q.ComputeStateProbability(currentState, chooser)]
            )
        else:
            stateData_nodrive = np.r_[stateData_nodrive, currentState.T]
            computedData_nodrive = np.r_[
                computedData_nodrive,
                np.array(
                    [[t_precise, q.ComputeStateProbability(currentState, chooser)]]
                ),
            ]
    if t_precise > (t_1 + τ):
        currentState: matrix = q.ComputeState(
            currentState,
            1 / precision,
            HamiltonianWithDrive2X2(omegaQ01_M, OmegaD, PhiD, A),
        )
        if k:
            k = not k
            stateData_drive2[0] = np.array(currentState.T)
            computedData_drive2[0] = np.array(
                [t_precise, q.ComputeStateProbability(currentState, chooser)]
            )
        else:
            stateData_drive2 = np.r_[stateData_drive2, currentState.T]
            computedData_drive2 = np.r_[
                computedData_drive2,
                np.array(
                    [[t_precise, q.ComputeStateProbability(currentState, chooser)]]
                ),
            ]

Computing ... : 100%|██████████| 17500/17500 [00:02<00:00, 8549.53it/s]


In [7]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=computedData_drive1[:, 0],
        y=computedData_drive1[:, 1],
        name="X(π/2) Drive",
        marker_color="red",
        mode="markers",
    )
)
fig.add_trace(
    go.Scatter(
        x=computedData_nodrive[:, 0],
        y=computedData_nodrive[:, 1],
        name="No Drive",
        marker_color="blue",
        mode="markers",
    )
)
fig.add_trace(
    go.Scatter(
        x=computedData_drive2[:, 0],
        y=computedData_drive2[:, 1],
        name="X(π/2) Drive",
        marker_color="green",
        mode="markers",
    )
)
fig.update_yaxes(
    range=[-0.1, 1.1],
    dtick=0.5,
)
fig.update_layout(
    title={
        "text": "Ramsey振荡",
        "y": 0.9,
        "x": 0.5,
        "xanchor": "center",
        "yanchor": "top",
    },
    xaxis_title="t(μs)",
    yaxis_title="0态概率",
    font=dict(color="black"),
    width=800,
)
fig.show()

In [8]:
Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(0, np.pi / 2, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig = go.Figure(data=[go.Mesh3d(x=x, y=y, z=z, opacity=0.3, color="#FFD88F")])

Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(np.pi / 2, np.pi, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig.add_trace(
    go.Mesh3d(
        x=x,
        y=y,
        z=z,
        opacity=0.3,
        color="#FFD88F",
    )
)

coo = []
for states in stateData_drive1:
    a: complexfloating = states[0, 0]
    b: complexfloating = states[0, 1]
    alpha: float = np.angle(a)
    beta: float = np.angle(b)
    phi: float = beta - alpha
    theta: float = 2 * np.arccos(np.abs(a))
    x: float = np.sin(theta) * np.cos(phi)
    y: float = np.sin(theta) * np.sin(phi)
    z: float = np.cos(theta)
    coo.append([x, y, z])
ndCoo: NDArray = np.array(coo)

fig.add_trace(
    go.Scatter3d(
        x=ndCoo[:, 0],
        y=ndCoo[:, 1],
        z=ndCoo[:, 2],
        mode="markers",
        name="X(π/2) Drive",
        marker=dict(
            color="red",
            size=4,
        ),
    )
)

coo = []
for states in stateData_nodrive:
    a: complexfloating = states[0, 0]
    b: complexfloating = states[0, 1]
    alpha: float = np.angle(a)
    beta: float = np.angle(b)
    phi: float = beta - alpha
    theta: float = 2 * np.arccos(np.abs(a))
    x: float = np.sin(theta) * np.cos(phi)
    y: float = np.sin(theta) * np.sin(phi)
    z: float = np.cos(theta)
    coo.append([x, y, z])
ndCoo: NDArray = np.array(coo)

fig.add_trace(
    go.Scatter3d(
        x=ndCoo[:, 0],
        y=ndCoo[:, 1],
        z=ndCoo[:, 2],
        mode="markers",
        name="No Drive",
        marker=dict(
            color="blue",
            size=4,
        ),
    )
)

coo = []
for states in stateData_drive2:
    a: complexfloating = states[0, 0]
    b: complexfloating = states[0, 1]
    alpha: float = np.angle(a)
    beta: float = np.angle(b)
    phi: float = beta - alpha
    theta: float = 2 * np.arccos(np.abs(a))
    x: float = np.sin(theta) * np.cos(phi)
    y: float = np.sin(theta) * np.sin(phi)
    z: float = np.cos(theta)
    coo.append([x, y, z])
ndCoo: NDArray = np.array(coo)

fig.add_trace(
    go.Scatter3d(
        x=ndCoo[:, 0],
        y=ndCoo[:, 1],
        z=ndCoo[:, 2],
        mode="markers",
        name="X(π/2) Drive",
        marker=dict(
            color="green",
            size=4,
        ),
    )
)

fig.update_traces(colorbar=dict(thickness=0), selector=dict(type="surface"))

fig.update_layout(
    title={
        "text": "量子比特态在布洛赫球上运动轨迹",
        "y": 0.9,
        "x": 0.5,
        "xanchor": "center",
        "yanchor": "top",
    },
    font=dict(color="black"),
    scene=dict(
        xaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(200, 200, 230)",
        ),
        yaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 200, 230)",
        ),
        zaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 230, 200)",
        ),
    ),
    scene_aspectmode="cube",
    width=800,
    height=800,
)

fig.show()

In [9]:
def ComputeRamseyFinalState(
    omegaQ01: float,
    omegaD: float,
    phiD: float,
    A: float,
    initialState: matrix,
    τ: float,
):
    T: float = (2 * np.pi) / A
    t_1: float = T / 4
    t_2: float = T / 4
    firstState: matrix = q.ComputeState(
        initialState, t_1, HamiltonianWithDrive2X2(omegaQ01, omegaD, phiD, A)
    )
    secondState: matrix = q.ComputeState(
        firstState, τ, HamiltonianWithoutDrive2X2(omegaQ01, omegaD)
    )
    finalState: matrix = q.ComputeState(
        secondState, t_2, HamiltonianWithDrive2X2(omegaQ01, omegaD, phiD, A)
    )
    return finalState

In [10]:
stateData: NDArray = array([[0.0j, 0.0j]])
measureTimes: int = 500
firstMeasurement: bool = True
numerator: float = 1.0
denominator: float = 1.0
τ: float = ((OmegaD - OmegaQ01) * numerator) / ((2 * np.pi) * denominator)
# τ = 0.001
for i in range(0, measureTimes):
    omegaQ01_Modified = OmegaQ01 + np.random.normal(0, 1)
    measuredState: matrix = ComputeRamseyFinalState(
        omegaQ01_Modified, OmegaD, PhiD, A, initialState, τ
    )
    if firstMeasurement:
        firstMeasurement = not firstMeasurement
        stateData[0] = np.array(measuredState.T)
    else:
        stateData = np.r_[stateData, measuredState.T]

In [11]:
coo = []
for states in stateData:
    a: complexfloating = states[0, 0]
    b: complexfloating = states[0, 1]
    alpha: float = np.angle(a)
    beta: float = np.angle(b)
    phi: float = beta - alpha
    theta: float = 2 * np.arccos(np.abs(a))
    x: float = np.sin(theta) * np.cos(phi)
    y: float = np.sin(theta) * np.sin(phi)
    z: float = np.cos(theta)
    coo.append([x, y, z])
ndCoo: NDArray = np.array(coo)

Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(0, np.pi / 2, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig = go.Figure(data=[go.Mesh3d(x=x, y=y, z=z, opacity=0.3, color="#FFD88F")])

Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(np.pi / 2, np.pi, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig.add_trace(
    go.Mesh3d(
        x=x,
        y=y,
        z=z,
        opacity=0.3,
        color="#FFD88F",
    )
)


fig.add_trace(
    go.Scatter3d(
        x=ndCoo[:, 0],
        y=ndCoo[:, 1],
        z=ndCoo[:, 2],
        mode="markers",
        marker=dict(
            color="red",
            size=4,
        ),
    )
)

fig.update_traces(colorbar=dict(thickness=0), selector=dict(type="surface"))

fig.update_layout(
    title={
        "text": "量子比特态在布洛赫球上运动轨迹",
        "y": 0.9,
        "x": 0.5,
        "xanchor": "center",
        "yanchor": "top",
    },
    font=dict(color="black"),
    scene=dict(
        xaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(200, 200, 230)",
        ),
        yaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 200, 230)",
        ),
        zaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 230, 200)",
        ),
    ),
    scene_aspectmode="cube",
    width=800,
    height=800,
)

fig.show()

In [12]:
measureTimes: int = 1000
firstMeasurement_outter: bool = True
firstMeasurement_inner: bool = True
precision: int = 15
numerator: float = 1.0
denominator: float = 1.0
startτ: float = 0.0
# endτ: float = ((OmegaD - OmegaQ01) * numerator) / ((2 * np.pi) * denominator)
endτ: float = 5.0
for t in tqdm(
    range(int(startτ * precision), int(endτ * precision) + 1),
    desc="Computing ... ",
    colour="#41F5D4",
):
    t_precise = t / precision
    counterForState_0: int = 0
    firstMeasurement_inner = True
    for i in range(0, measureTimes):
        omegaQ01_Modified = OmegaQ01 + np.random.normal(0, 1)
        measuredState: matrix = ComputeRamseyFinalState(
            omegaQ01_Modified, OmegaD, PhiD, A, initialState, t_precise
        )
        coefficientSquared: float = (np.abs(measuredState[0, 0])) ** 2
        numRandom: float = np.random.random()
        if numRandom <= coefficientSquared:
            counterForState_0 = counterForState_0 + 1
        if firstMeasurement_inner:
            firstMeasurement_inner = not firstMeasurement_inner
            stateData: NDArray = array(measuredState.T)
        else:
            stateData: NDArray = np.r_[stateData, measuredState.T]
    firstMeasurement_inner = True
    for states in stateData:
        a: complexfloating = states[0, 0]
        b: complexfloating = states[0, 1]
        alpha: float = np.angle(a)
        beta: float = np.angle(b)
        phi: float = beta - alpha
        theta: float = 2 * np.arccos(np.abs(a))
        x: float = np.sin(theta) * np.cos(phi)
        y: float = np.sin(theta) * np.sin(phi)
        z: float = np.cos(theta)
        if firstMeasurement_inner:
            firstMeasurement_inner = not firstMeasurement_inner
            coordinateData: NDArray = array([[x, y, z]])
        else:
            coordinateData: NDArray = np.r_[coordinateData, [[x, y, z]]]
    meanX: float = np.sum(coordinateData[:, 0]) / measureTimes
    meanY: float = np.sum(coordinateData[:, 1]) / measureTimes
    meanZ: float = np.sum(coordinateData[:, 2]) / measureTimes
    probabilityState_0: float = counterForState_0 / measureTimes
    if firstMeasurement_outter:
        firstMeasurement_outter = not firstMeasurement_outter
        probabilityData: NDArray = np.array([[t_precise, probabilityState_0]])
        meanCoordinateData: NDArray = np.array([[meanX, meanY, meanZ]])
    else:
        probabilityData: NDArray = np.r_[
            probabilityData, [[t_precise, probabilityState_0]]
        ]
        meanCoordinateData: NDArray = np.r_[meanCoordinateData, [[meanX, meanY, meanZ]]]

Computing ... : 100%|██████████| 76/76 [00:18<00:00,  4.19it/s]


In [13]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=probabilityData[:, 0],
        y=probabilityData[:, 1],
        name="state 0 probability",
        mode="markers",
    )
)
fig.update_yaxes(
    range=[-0.1, 1.1],
    dtick=0.5,
)
fig.update_layout(
    title={
        "text": "Ramsey振荡",
        "y": 0.9,
        "x": 0.5,
        "xanchor": "center",
        "yanchor": "top",
    },
    xaxis_title="t(μs)",
    yaxis_title="0态概率",
    font=dict(color="black"),
    width=800,
)
fig.show()

In [14]:
Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(0, np.pi / 2, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig = go.Figure(data=[go.Mesh3d(x=x, y=y, z=z, opacity=0.3, color="#FFD88F")])

Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(np.pi / 2, np.pi, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig.add_trace(
    go.Mesh3d(
        x=x,
        y=y,
        z=z,
        opacity=0.3,
        color="#FFD88F",
    )
)


fig.add_trace(
    go.Scatter3d(
        x=meanCoordinateData[:, 0],
        y=meanCoordinateData[:, 1],
        z=meanCoordinateData[:, 2],
        mode="markers",
        name="Mixed States",
        marker=dict(
            color="red",
            size=4,
        ),
    )
)


fig.update_traces(colorbar=dict(thickness=0), selector=dict(type="surface"))

fig.update_layout(
    title={
        "text": "混态",
        "y": 0.9,
        "x": 0.5,
        "xanchor": "center",
        "yanchor": "top",
    },
    font=dict(color="black"),
    scene=dict(
        xaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(200, 200, 230)",
        ),
        yaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 200, 230)",
        ),
        zaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 230, 200)",
        ),
    ),
    scene_aspectmode="cube",
    width=800,
    height=800,
)

fig.show()